In [1]:
# импорт
import requests, base64, datetime, time
from urllib.parse import urlencode

import os
os.environ.setdefault('DJANGO_SETTINGS_MODULE', 'rrp.settings')
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"

import django
django.setup()
from tracks.models import *

In [2]:
Application_name = 'russian_rock_playlist'
USER_NAME        = 'hostbetxiaomi'
API_KEY          = '5a0ae1296c8d4388a66c507ba27e92aa'
Shared_secret    = 'aba5cc8b972170d1e8ab5eb4188a5524'

### Парсинг тегов для каждого трека с Last FM

In [3]:
from slugify import slugify
import pandas as pd
path      = r'D:\копия\Черновики\rrp\tracks.xlsx'
tags_path = r'D:\копия\Черновики\rrp\tags.txt'

In [4]:
df = pd.read_excel(path, sheet_name='parse').sort_values('track_id')

In [5]:
def collect_tags():

    start  = 0
    finish = len(df)

    while start < finish:
        for i in range (start, finish):
                row = df.iloc[i, :]
                band_name  = row[0].strip()
                track_name = row[1].replace(' - Live', '').replace(' (Live)', '').strip()
                track_id   = row[2].strip()
                print(f'Поиск тэгов для трека "{band_name}" - "{track_name}"')
        
                try:
                    time.sleep(4)
                    lastFM_endpoint   = "http://ws.audioscrobbler.com/2.0/?method=track.gettoptags&artist="
                    lastFM_lookup_url = f"{lastFM_endpoint}{band_name}&track={track_name}&api_key={API_KEY}&format=json"
                    lastFM_request    = requests.get(lastFM_lookup_url).json()
                    
                    tags_list = []
                    for index, tag in enumerate( lastFM_request['toptags']['tag'][:10] ):
                        tags_list.append(f'{tag["name"].lower()},{tag["count"]}')
                        if len(tags_list) == 0:
                            print(f'--- Список тэгов пуст')
                    

                    with open(tags_path, 'a') as file:
                        file.write(f'{track_id},{tags_list}\n')

                    print(f'Добавлены тэги для трека "{band_name}" - "{track_name}"')
                    start += 1

                except:
                    print(f'!!! Не найдены тэги для трека "{band_name}" - "{track_name}", start = {start}')

    print('Тэги добавлены')


collect_tags()


Поиск тэгов для трека "Крематорий" - "Разбитое сердце"
Добавлены тэги для трека "Крематорий" - "Разбитое сердце"
Поиск тэгов для трека "Зимовье Зверей" - "Песня зверей в хлеву"
Добавлены тэги для трека "Зимовье Зверей" - "Песня зверей в хлеву"
Поиск тэгов для трека "Слот" - "Эмаль"
Добавлены тэги для трека "Слот" - "Эмаль"
Поиск тэгов для трека "Тени Свободы" - "Please the Higher"
Добавлены тэги для трека "Тени Свободы" - "Please the Higher"
Поиск тэгов для трека "Секрет" - "Лети"
Добавлены тэги для трека "Секрет" - "Лети"
Поиск тэгов для трека "Операция Пластилин" - "Флоксы"
Добавлены тэги для трека "Операция Пластилин" - "Флоксы"
Поиск тэгов для трека "Конец фильма" - "Шоссе"
Добавлены тэги для трека "Конец фильма" - "Шоссе"
Поиск тэгов для трека "Кирпичи" - "Cut the Heads Off"
!!! Не найдены тэги для трека "Кирпичи" - "Cut the Heads Off", start = 2371
Поиск тэгов для трека "Факторы" - "Liar Swindler Provocateur"
Добавлены тэги для трека "Факторы" - "Liar Swindler Provocateur"
Поиск 

### Парсинг тегов для каждого трека 

In [17]:
import pandas as pd
import numpy as np

In [18]:
track_ids = []
with open(r'D:\копия\Черновики\rrp\track_ids.txt') as file:
    for line in file.readlines():
        track_ids.append(line.strip())

In [19]:
tags_ids = []
with open(r'D:\копия\Черновики\rrp\track_tag_list.txt') as file:
    for line in file.readlines():
        tags_ids.append(line.strip())

In [20]:
df = pd.DataFrame(np.zeros( (len(track_ids), len(tags_ids)), dtype='i'), columns=tags_ids, index=track_ids)  

In [21]:
with open(r'D:\копия\Черновики\rrp\tags_copy.txt') as file:
    for line in file.readlines():

        id, tags = line.split(';')[0], line.split(';')[1]
        if len(tags) > 3:
            tags = tags.replace('[', '').replace(']', '').replace("'", '').replace('\n', '')

            try:
                for tag in tags.split(','):

                    k, v = tag.split(':')

                    df.loc[id, k] += int(v)
            except:
                pass

In [22]:
from pandas import ExcelWriter
writer = ExcelWriter(r'D:\копия\Черновики\rrp\tracks_tags.xlsx')
df.to_excel(writer,'tags')
writer.save()

### Парсинг жанров для каждой группы

In [23]:
band_ids = []
with open(r'D:\копия\Черновики\rrp\bands_genres.txt') as file:
    for line in file.readlines():
        band_ids.append(line.split('	')[0].strip())

In [2]:
genres_ids = []
with open(r'D:\копия\Черновики\rrp\band_genres.txt') as file:
    for line in file.readlines():
        genres_ids.append(line.strip())

In [24]:
df = pd.DataFrame(np.zeros( (len(band_ids), len(genres_ids)), dtype='i'), columns=genres_ids, index=band_ids)  

In [25]:
with open(r'D:\копия\Черновики\rrp\bands_genres.txt') as file:
    for line in file.readlines():
        # print(line)
        id, genres = line.split('	')
        # print(genres)
        try:
            for genre in genres.split(','):
                df.loc[id, genre.strip()] = 1
        except:
            pass

In [26]:
from pandas import ExcelWriter
writer = ExcelWriter(r'D:\копия\Черновики\rrp\band_genres.xlsx')
df.to_excel(writer,'genres')
writer.save()

### Парсинг текстов песен

In [3]:
from bs4 import BeautifulSoup as bs

In [ ]:
def vse_pesni(vse_pesni_req):
    try:
        vse_pesni_html = bs(vse_pesni_req.text, 'lxml')

        song_text = vse_pesni_html.find('div', id='page') \
                                .find('div', id='main') \
                                .find('div', id='content') \
                                .find('div', class_='entry-content') \
                                .find('div', class_='song_text')

        song_text = (str(song_text.__dict__['contents'][0]) + \
                    str(song_text.__dict__['contents'][2])) \
                    .replace('\n', '')\
                    .replace('\t', '')\
                    .replace('\r', ' ')\
                    .strip()

        return song_text
    except:
        return None


def lyricshare(lyricshare_req):
    try:
        lyricshare_html = bs(lyricshare_req.text, 'lxml')

        song_text = lyricshare_html.find('div', id='wrapper') \
                                .find('div', class_='wrapper-inner') \
                                .find('div', id='colone-container') \
                                .find('div', class_='col-one') \
                                .find('div', id='textPesniDiv') \
                                .find('div', id='textPesniDiv-outer') \
                                .find('p', id='textpesni')

        song_text = song_text.text.replace('ПРИПЕВ', '').replace('\n', ' ').strip()

        return song_text
    except:
        return None


def megalyrics(megalyrics_req):
    try:
        megalyrics_html = bs(megalyrics_req.text, 'lxml')

        song_text = megalyrics_html.find('div', id='wrap') \
                                .find('div', id='page') \
                                .find('div', id='page_main') \
                                .find('div', id='songs_show') \
                                .find('div', class_='wrap') \
                                .find('div', id='txt') \
                                .find('div', class_='text separate') \
                                .find('div', class_='text_inner')

        song_text = str(song_text).replace('<br/>', ' ') \
                                  .replace('<div class="text_inner">', '') \
                                  .replace('<div id="native_roll">', '') \
                                  .replace('</div>', '') \
                                  .strip()
        return song_text
    except:
        return None
                                

track_list = Track.objects.all().values_list('band_id', 'band_name', 
                                            'album_id', 'album_name',
                                            'track_id', 'track_name') \
                                            .order_by('track_id')[:1000]
for track in track_list:
    band_id    = track[0]   # '2GUwb2rxMKePzxDi94EEoZ'
    band_name  = track[1]   # 'Ночные снайперы'
    album_id   = track[2]   # '3z9HvGReqatzDLy2DL1w18'
    album_name = track[3]   # 'Koshika'
    track_id   = track[4]   # '0032CHOcRVH98tHdVYFXRN'
    track_name = track[5]   # 'катастрофически'

    print(f'Поиск текста песни "{band_name}" - "{track_name}"')

    text_dict = { 
        'band_id'    : band_id,
        'band_name'  : band_name,
        'album_id'   : album_id,
        'album_name' : album_name,
        'track_id'   : Track.objects.get(track_id=track_id),
        'track_name' : track_name
    }
        
    band  = slugify(band_name).strip()
    track = slugify(track_name).replace('-live', '').replace('(live)', '') \
            .replace('(remix)', '').strip('- Original mix', '').strip()

    time.sleep(3)

    try:
        vse_pesni_req  = requests.get(f'https://vse-pesni.com/song/{band}-{track}/')
    except:
        print(f'--- !!! Нет ответа от "vse_pesni"')
        vse_pesni_req = None

    try:
        lyricshare_req = requests.get(f'http://www.lyricshare.net/ru/{band}/{track}.html')
    except:
        print(f'--- !!! Нет ответа от "lyricshare"')
        lyricshare_req = None

    try:
        megalyrics_req = requests.get(f'http://www.megalyrics.ru/lyric/{band}/{track}.htm')
    except:
        print(f'--- !!! Нет ответа от "megalyrics"')
        megalyrics_req = None

    vse_pesni_result  = vse_pesni(vse_pesni_req)
    lyricshare_result = lyricshare(lyricshare_req)
    megalyrics_result = megalyrics(megalyrics_req)

    if vse_pesni_result:
        text_dict.update({'song_text': vse_pesni_result})        
        print(f'Загружен текст с сайта "vse_pesni"')

    elif lyricshare_result:
        text_dict.update({'song_text': lyricshare_result})        
        print(f'Загружен текст с сайта "lyricshare"')

    elif megalyrics_result:
        text_dict.update({'song_text': megalyrics_result})        
        print(f'Загружен текст с сайта "megalyrics"')

    else:
        print(f'!!! Текст песни "{band_name}" - "{track_name}" не найден')

    # создание записи в БД
    Text.objects.create(**text_dict)
